In [11]:
!pip install opencv-python dlib --quiet

In [12]:
!wget http://dlib.net/files/shape_predictor_68_face_landmarks.dat.bz2
!bzip2 -d shape_predictor_68_face_landmarks.dat.bz2


--2025-05-04 19:26:37--  http://dlib.net/files/shape_predictor_68_face_landmarks.dat.bz2
Resolving dlib.net (dlib.net)... 107.180.26.78
Connecting to dlib.net (dlib.net)|107.180.26.78|:80... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: https://dlib.net/files/shape_predictor_68_face_landmarks.dat.bz2 [following]
--2025-05-04 19:26:37--  https://dlib.net/files/shape_predictor_68_face_landmarks.dat.bz2
Connecting to dlib.net (dlib.net)|107.180.26.78|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 64040097 (61M)
Saving to: ‘shape_predictor_68_face_landmarks.dat.bz2’

shape_predictor_68_ 100%[===================>]  61.07M  16.8MB/s    in 3.6s    

2025-05-04 19:26:41 (16.8 MB/s) - ‘shape_predictor_68_face_landmarks.dat.bz2’ saved [64040097/64040097]



In [17]:
import cv2
import dlib
import os
import numpy as np
import time
from IPython.display import display, Javascript
from base64 import b64decode, b64encode
from google.colab.output import eval_js

In [18]:
# EAR - Eye Aspect Ratio
def eye_aspect_ratio(eye):
    A = np.linalg.norm(eye[1] - eye[5])
    B = np.linalg.norm(eye[2] - eye[4])
    C = np.linalg.norm(eye[0] - eye[3])
    return (A + B) / (2.0 * C)

In [19]:
# Funções para câmera via JS
def setup_camera():
    js = """
    var div = document.createElement('div');
    div.innerHTML = `
      <video id="webcam" autoplay playsinline width=640 height=480 style="display:none;"></video>
      <canvas id="canvas" width=640 height=480 style="display:none;"></canvas>
      <img id="output" style="display:block;margin:auto;border:1px solid #ccc;">
    `;
    document.body.appendChild(div);
    const video = document.getElementById('webcam');
    const canvas = document.getElementById('canvas');
    const ctx = canvas.getContext('2d');
    navigator.mediaDevices.getUserMedia({video: true}).then(stream => {
      video.srcObject = stream;
    });
    window.captureFrame = () => {
      ctx.drawImage(video, 0, 0, canvas.width, canvas.height);
      return canvas.toDataURL('image/jpeg');
    };
    """
    display(Javascript(js))
    time.sleep(2)

def capture_frame():
    js = "captureFrame();"
    data = eval_js(js)
    content = data.split(',')[1]
    img_bytes = b64decode(content)
    return cv2.imdecode(np.frombuffer(img_bytes, np.uint8), cv2.IMREAD_COLOR)

def update_display(frame):
    _, buffer = cv2.imencode('.jpg', frame)
    b64 = b64encode(buffer).decode('utf-8')
    js = f'document.getElementById("output").src = "data:image/jpeg;base64,{b64}";'
    display(Javascript(js))

# Criar dataset
def criar_dataset(nome, num_frames=20, intervalo=0.3, dataset_path="dataset"):
    os.makedirs(os.path.join(dataset_path, nome), exist_ok=True)
    detector = dlib.get_frontal_face_detector()
    setup_camera()
    capturados = 0

    while capturados < num_frames:
        frame = capture_frame()
        gray = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)
        faces = detector(gray)

        for face in faces:
            x, y, w, h = face.left(), face.top(), face.width(), face.height()
            roi = gray[y:y+h, x:x+w]
            roi = cv2.resize(roi, (200, 200))
            roi = cv2.equalizeHist(roi)
            path = os.path.join(dataset_path, nome, f"{capturados:03}.jpg")
            cv2.imwrite(path, roi)
            capturados += 1
            cv2.rectangle(frame, (x, y), (x+w, y+h), (0,255,0), 2)
            update_display(frame)
            time.sleep(intervalo)
            break

        update_display(frame)
        time.sleep(intervalo)

# Treinamento
def treinar_reconhecedor(dataset_path="dataset"):
    recognizer = cv2.face.LBPHFaceRecognizer_create()
    faces, labels, label_dict = [], [], {}
    label_id = 0

    for pessoa in os.listdir(dataset_path):
        pessoa_path = os.path.join(dataset_path, pessoa)
        if not os.path.isdir(pessoa_path): continue
        label_dict[label_id] = pessoa

        for img in os.listdir(pessoa_path):
            path = os.path.join(pessoa_path, img)
            img_gray = cv2.imread(path, cv2.IMREAD_GRAYSCALE)
            faces.append(img_gray)
            labels.append(label_id)

        label_id += 1

    recognizer.train(faces, np.array(labels))
    return recognizer, label_dict

# Loop de reconhecimento com liveness
def reconhecimento_loop(recognizer, label_dict):
    detector = dlib.get_frontal_face_detector()
    predictor = dlib.shape_predictor("shape_predictor_68_face_landmarks.dat")
    setup_camera()

    try:
        while True:
            frame = capture_frame()
            gray = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)
            faces = detector(gray)

            for face in faces:
                x, y, w, h = face.left(), face.top(), face.width(), face.height()
                roi = gray[y:y+h, x:x+w]
                roi = cv2.resize(roi, (200, 200))
                roi = cv2.equalizeHist(roi)
                label, conf = recognizer.predict(roi)
                nome = label_dict[label] if conf < 50 else "Desconhecido"

                shape = predictor(gray, face)
                coords = np.array([[shape.part(i).x, shape.part(i).y] for i in range(68)])
                left_eye = coords[42:48]
                right_eye = coords[36:42]
                ear = (eye_aspect_ratio(left_eye) + eye_aspect_ratio(right_eye)) / 2.0
                liveness = "Piscando (vivo)" if ear < 0.2 else "Olhos abertos"

                cv2.rectangle(frame, (x, y), (x+w, y+h), (0,255,0), 2)
                cv2.putText(frame, f"{nome} - {liveness}", (x, y-10),
                            cv2.FONT_HERSHEY_SIMPLEX, 0.6, (255,255,255), 2)

            update_display(frame)
            time.sleep(0.2)

    except KeyboardInterrupt:
        print("Reconhecimento encerrado.")

In [21]:
# criando diretorio de treinamento
# Obs. 1: por questão da permissão de acesso à camera, pode ser necessário interromper a primeira execução e executar novamente para começar a capturar
# Obs. 2: As imagens capturadas ficarão salvas em "dataset/nome_informado"
name = input("Informe seu nome para o treinamento: ")
num_frames = 20 # quantidade de imagens que serão capturadas
criar_dataset(name, num_frames=num_frames,intervalo=0.2)


Informe seu nome para o treinamento: Marcella


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [22]:
recognizer, label_dict = treinar_reconhecedor("dataset")
reconhecimento_loop(recognizer, label_dict)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Reconhecimento encerrado.
